In [1]:
import datetime
import _speed_utils as speed_utils
import dask.dataframe as dd
import numpy as np
import geopandas as gpd
import pandas as pd
from segment_speed_utils import gtfs_schedule_wrangling, helpers, segment_calcs,sched_rt_utils
from segment_speed_utils.project_vars import (
    COMPILED_CACHED_VIEWS,
    PROJECT_CRS,
    SEGMENT_GCS,
    analysis_date,
)
from scripts import (A1_sjoin_vp_segments, A2_valid_vehicle_positions)
from shared_utils import calitp_color_palette as cp

/opt/conda/lib/python3.9/site-packages/geopandas/_compat.py:123: UserWarning: The Shapely GEOS version (3.11.1-CAPI-1.17.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(
/home/jovyan/data-analyses/rt_segment_speeds/_speed_utils.py:4: UserWarning: Shapely 2.0 is installed, but because PyGEOS is also installed, GeoPandas will still use PyGEOS by default for now. To force to use and test Shapely 2.0, you have to set the environment variable USE_PYGEOS=0. You can do this before starting the Python process, or in your code before importing geopandas:

import os
os.environ['USE_PYGEOS'] = '0'
import geopandas

In a future release, GeoPandas will switch to using Shapely by default. If you are using PyGEOS directly (calling PyGEOS functions on geometries from GeoPandas), this will then stop working and you are encouraged to migrate from PyGEOS to Shapely 2.0 (https://shapely.readthedocs.io/en/latest/

In [2]:
pd.options.display.max_columns = 100
pd.options.display.float_format = "{:.2f}".format
pd.set_option("display.max_rows", None)
pd.set_option("display.max_colwidth", None)

In [3]:
CONFIG_PATH = './scripts/config.yml'

In [4]:
STOP_SEG_DICT = helpers.get_parameters(CONFIG_PATH, "stop_segments")

In [5]:
analysis_date = '2023-07-12'

### Observations (7/12)
* Step 1: Flagging
    * There are 2,704,812 rows in the dataframe original. About 10% of those rows are flagged as having zeroes in meters elapsed and seconds elapsed. 
    * There are around 4566 routes. About 57% of these routes had at least one trip with one or more rows flagged as zero.
* I took 2 passes at trying to understand why both these columns recorded zeroes.

* Step 2: `vp_pared_stops`. 
    * I grouped `vp_pared_stops` by 'shape_array_key','trip_id', and 'location_timestamp_local' OR `x` and `y`. I counted the number of unique stop sequences after grouping. If this trio had more than one unique stop sequence, that meant the timestamp or location recorded between sequences was duplicated.
    * Only around 9% of rows were flagged as having (obviously) repeated timestamps and locations. 
    * For all of these rows, both the timestamp and location were duplicated. 
    * All the routes that were flagged in step one needed a further look in step 3.
    
* Step 3: `vp_usable`
    * For one route and trip, find: all the recorded vehicle positions, sjoin of vps to segments,
    and the first and last points kept. 
    * Plot the three gdfs in a map to visually inspect what's happening.
    * Compare the sample route and trips with the trip with the highest percentage of non division by 0 rows to see what's going on. 
    
* Buckets of errors (all based on `stage0 vp`). 
    * There is only one recorded point in that segment in the raw data.
        * Fix: use the timestamp that comes after it.
        * <img src= "./speeds_images/only_one_pt_collected.png" width = 300>
    * Points are shared between segments
        * Use p20/p50/p80.
        * <img src= "./speeds_images/shared_vp.png" width = 300>
    * Points recorded are really far out and they don't touch the buffered segments.
        * Fix: figure out % of vehicle positions that are too far out.
        * <img src= "./speeds_images/dots_not_on_seg.png" width = 300>
    * No data captured for that segment at all.
        * Use p20/p50/p80. 
        * <img src= "./speeds_images/no_dots_collected.png" width = 300> 

### Flagging

In [6]:
# Flagged: all the rows in the df flagged
# divide_by_zero: only the rows that have 0 for meters and sec elapsed
# trips_count: % of trips with 1+ division by 0 row for a route
# route_most_populated_df: the trip for a route with the smallest % of rows that are divided by 0
flagged, divide_by_zero, trips_count, route_most_populated_df = speed_utils.flagging_stage(analysis_date)

2023-07-18 17:10:58.688563
There are 2498742 rows in the original dataframe
sec_cat      meters_cat    
sec is avg   meters is avg     1886119
             meters is high      79418
             meters is low      131688
sec is high  meters is avg       61187
             meters is high      45520
             meters is low       18238
sec is low   meters is low      276572
dtype: int64
ok                 78.66
division by 0      11.07
meters too low      6.00
seconds too high    4.27
Name: flag, dtype: float64
23779 unique trips flagged.
2494 routes flagged out of 4087.
61.02275507707364 routes have 1+ row that has zeroes for meters/sec elapsed
14 operators are not flagged.
38.97724492292635% of routes have 1+ division by 0 row
Took 0:01:45.954144


In [7]:
divide_by_zero.loop_or_inlining.value_counts()

0    276572
Name: loop_or_inlining, dtype: int64

### Fix 1  - % of vehicle positions that are too far away from the shapes to be joined

#### SJOIN 
* Valid trips that are `sjoin` to segments.

In [8]:
USABLE_VP = STOP_SEG_DICT["stage1"]
INPUT_FILE_PREFIX = STOP_SEG_DICT["stage2"]
GROUPING_COL = STOP_SEG_DICT["grouping_col"]

In [9]:
normal_shapes = A2_valid_vehicle_positions.identify_stop_segment_cases(
        analysis_date, GROUPING_COL, 0)

In [10]:
abnormal_shapes = A2_valid_vehicle_positions.identify_stop_segment_cases(
        analysis_date, GROUPING_COL, 1)

In [11]:
# datetime.datetime.now() 

In [12]:
# Using A2 since I need the VPs to sjoin
# Only the pared down stops are saved out
"""
usable_abnormal_vp = A2_valid_vehicle_positions.merge_usable_vp_with_sjoin_vpidx(
        abnormal_shapes,
        f"{USABLE_VP}_{analysis_date}",
        f"{INPUT_FILE_PREFIX}_{analysis_date}",
        GROUPING_COL
    )

 """   

'\nusable_abnormal_vp = A2_valid_vehicle_positions.merge_usable_vp_with_sjoin_vpidx(\n        abnormal_shapes,\n        f"{USABLE_VP}_{analysis_date}",\n        f"{INPUT_FILE_PREFIX}_{analysis_date}",\n        GROUPING_COL\n    )\n\n '

In [13]:
#usable_abnormal_vp = usable_abnormal_vp.assign(
#    identifier = usable_abnormal_vp.gtfs_dataset_key.astype(str) + '/' + usable_abnormal_vp.shape_array_key.astype(str) + '/' + usable_abnormal_vp.trip_id.astype(str)
#)

In [14]:
#datetime.datetime.now() 

In [15]:
#agg = usable_abnormal_vp.groupby(['identifier']).vp_idx.nunique()

In [16]:
# agg = agg.compute()

In [17]:
#agg2 = agg.to_frame()

In [18]:
#agg3 = agg2.reset_index()

In [19]:
#agg3.shape

In [20]:
#agg3.sample()

In [21]:
#agg3["gtfs_dataset_key"] = agg3["index"].str.split("/").str[0]

In [22]:
#agg3["trip_id"] = agg3["index"].str.split("/").str[2]

In [23]:
#agg3 = agg3.drop(columns = ['index'])

In [24]:
#agg3 = agg3.rename(columns = {'vp_idx':'number_of_unique_vps_sjoin'})

In [25]:
#agg3.to_parquet(
#    f"{SEGMENT_GCS}special_vps_testing.parquet"
#)

In [26]:
#agg3 = pd.read_parquet(f"{SEGMENT_GCS}normalvps_testing.parquet")

In [27]:
normal = pd.read_parquet(f"{SEGMENT_GCS}normal_vps_testing.parquet")

In [28]:
normal = normal.drop(columns = ['identifier'])

In [29]:
special = pd.read_parquet(f"{SEGMENT_GCS}special_vps_testing.parquet")

In [30]:
sjoin_results = pd.concat([special, normal])

In [31]:
sjoin_results.sample()

number_of_unique_vps_sjoin                  gtfs_dataset_key  \
20375                         297  65d9589130415c685b89f4f7c2d8bd7e   

                    trip_id  
20375  10251001711149-DEC22

#### Crosswalk

In [32]:
TRIP_GROUPING_COLS = STOP_SEG_DICT["trip_grouping_cols"]

In [33]:
crosswalk = sched_rt_utils.crosswalk_scheduled_trip_grouping_with_rt_key(
        analysis_date, 
        ["feed_key", "trip_id"] + TRIP_GROUPING_COLS
    )

In [34]:
crosswalk = crosswalk.compute()

In [35]:
crosswalk.sample()

feed_key                trip_id  \
63433  79be71d17d4631e5d8d76a5c4eed7323  10018003391631-JUNE23   

                        shape_array_key                  gtfs_dataset_key  
63433  6869e7b2a0de94c39f7f43434115f594  65d9589130415c685b89f4f7c2d8bd7e

#### A1 sjoin
* Would use this instead of A2 result?

In [36]:
# This is the end result from A1_sjoin
# Not using this since no trip_id information
f"{SEGMENT_GCS}vp_sjoin/{INPUT_FILE_PREFIX}_{analysis_date}"

'gs://calitp-analytics-data/data-analyses/rt_segment_speeds/vp_sjoin/vp_stop_segment_2023-07-12'

In [37]:
vp_to_seg = dd.read_parquet(
      f"{SEGMENT_GCS}vp_sjoin/{INPUT_FILE_PREFIX}_{analysis_date}",
    )

In [38]:
vp_to_seg = vp_to_seg.compute()

In [39]:
vp_to_seg.sample()

vp_idx                   shape_array_key  stop_sequence
1139271  6229568  39a22de0800f09526fc5128c91086dfa             45

In [40]:
len(vp_to_seg)

24973725

In [41]:
# len(vp_to_seg[vp_to_seg.shape_array_key == "aafeeea21721ee9be95c6f794dabdac3"])

#### Usable VPS

In [42]:
usable_vp = dd.read_parquet(
        f"{SEGMENT_GCS}{USABLE_VP}_{analysis_date}"
    )

In [43]:
type(usable_vp)

dask.dataframe.core.DataFrame

In [44]:
# 14,579,242
# len(usable_vp)

In [45]:
# https://stackoverflow.com/questions/49139371/slicing-out-a-few-rows-from-a-dask-dataframe
npart = round(len(usable_vp)/1_000_000)
parted_usable_vp = usable_vp.repartition(npartitions=npart)

In [46]:
npart

15

##### Test 1

In [47]:
test = parted_usable_vp.partitions[0]

In [48]:
test = test.assign(
    identifier = test.gtfs_dataset_key.astype(str) + '/' + test.trip_id.astype(str)
)

In [49]:
# Using 
test = test.groupby(['identifier']).vp_idx.nunique()

In [50]:
test = test.compute()

In [51]:
test.head()

identifier
00accf770009aafd5dc103ff2eeddb37/t_5634826_b_80735_tn_0    189
00accf770009aafd5dc103ff2eeddb37/t_5634829_b_80735_tn_0    147
00accf770009aafd5dc103ff2eeddb37/t_5634830_b_80735_tn_0    164
00accf770009aafd5dc103ff2eeddb37/t_5634831_b_80735_tn_0    108
00accf770009aafd5dc103ff2eeddb37/t_5634834_b_80735_tn_0    198
Name: vp_idx, dtype: int64

In [52]:
test = test.to_frame()

In [53]:
test = test.reset_index()

In [54]:
test["gtfs_dataset_key"] = test["identifier"].str.split("/").str[0]

In [55]:
test["trip_id"] = test["identifier"].str.split("/").str[1]

In [56]:
test.head()

identifier  vp_idx  \
0  00accf770009aafd5dc103ff2eeddb37/t_5634826_b_80735_tn_0     189   
1  00accf770009aafd5dc103ff2eeddb37/t_5634829_b_80735_tn_0     147   
2  00accf770009aafd5dc103ff2eeddb37/t_5634830_b_80735_tn_0     164   
3  00accf770009aafd5dc103ff2eeddb37/t_5634831_b_80735_tn_0     108   
4  00accf770009aafd5dc103ff2eeddb37/t_5634834_b_80735_tn_0     198   

                   gtfs_dataset_key                 trip_id  
0  00accf770009aafd5dc103ff2eeddb37  t_5634826_b_80735_tn_0  
1  00accf770009aafd5dc103ff2eeddb37  t_5634829_b_80735_tn_0  
2  00accf770009aafd5dc103ff2eeddb37  t_5634830_b_80735_tn_0  
3  00accf770009aafd5dc103ff2eeddb37  t_5634831_b_80735_tn_0  
4  00accf770009aafd5dc103ff2eeddb37  t_5634834_b_80735_tn_0

##### Test2

In [57]:
test2 = parted_usable_vp.partitions[0]

In [58]:
test2 = test2.compute()

#### Merge test1 with A2sjoin results

In [59]:
len(sjoin_results)

68339

In [60]:
sjoin_results.gtfs_dataset_key.nunique(),sjoin_results.trip_id.nunique()

(80, 66642)

In [61]:
test.gtfs_dataset_key.nunique(),test.trip_id.nunique()

(5, 672)

In [62]:
test.sample()

identifier  vp_idx  \
180  00e412908245377894949d292fb79610/t_1523670_b_30719_tn_0      80   

                     gtfs_dataset_key                 trip_id  
180  00e412908245377894949d292fb79610  t_1523670_b_30719_tn_0

In [63]:
sjoin_results.sample()

number_of_unique_vps_sjoin                  gtfs_dataset_key  \
10669                         372  65d9589130415c685b89f4f7c2d8bd7e   

                    trip_id  
10669  10004003181020-DEC22

In [64]:
# How is it possible there are some that are right_only?
# Lots of left only results b/c this is the full df. 
# test is just a subset
pd.merge(sjoin_results, test, on = ['gtfs_dataset_key','trip_id'], how = 'outer', indicator = True)[['_merge']].value_counts()

_merge    
left_only     67827
both            512
right_only      160
dtype: int64

In [65]:
merge1 =  pd.merge(test, sjoin_results,  on = ['gtfs_dataset_key','trip_id'], how = 'inner')

In [66]:
merge1.sample()

identifier  vp_idx  \
487  0faa34840bb65e96b7f83b7f379c2edd/7_Trip1_H_COVID     111   

                     gtfs_dataset_key          trip_id  \
487  0faa34840bb65e96b7f83b7f379c2edd  7_Trip1_H_COVID   

     number_of_unique_vps_sjoin  
487                          86

In [67]:
merge1['percent_of_positions_retained'] = merge1.number_of_unique_vps_sjoin/merge1.vp_idx * 100

In [68]:
merge1.percent_of_positions_retained.describe()

count    512.00
mean      91.00
std       64.42
min       14.56
25%       69.09
50%       89.52
75%       98.85
max     1275.00
Name: percent_of_positions_retained, dtype: float64

In [69]:
merge2 =  pd.merge(merge1, crosswalk,  on = ['gtfs_dataset_key','trip_id'], how = 'left')

##### Why are 94 of the rows over 100??

In [70]:
merge2.sample(5)

identifier  vp_idx  \
376          0af37e731f00a843fb9a0fe286f8d958/1093640     297   
273          0af37e731f00a843fb9a0fe286f8d958/1093481     125   
253          0af37e731f00a843fb9a0fe286f8d958/1093446     129   
220          0af37e731f00a843fb9a0fe286f8d958/1093411     117   
478  0faa34840bb65e96b7f83b7f379c2edd/6_Trip1_H_COVID     120   

                     gtfs_dataset_key          trip_id  \
376  0af37e731f00a843fb9a0fe286f8d958          1093640   
273  0af37e731f00a843fb9a0fe286f8d958          1093481   
253  0af37e731f00a843fb9a0fe286f8d958          1093446   
220  0af37e731f00a843fb9a0fe286f8d958          1093411   
478  0faa34840bb65e96b7f83b7f379c2edd  6_Trip1_H_COVID   

     number_of_unique_vps_sjoin  percent_of_positions_retained  \
376                         212                          71.38   
273                         153                         122.40   
253                         110                          85.27   
220                         112                          95.73   
478                          82                          68.33   

                             feed_key                   shape_array_key  
376  7f718ddcc08a28370fbcd1cbe59c4033  0c010a8c84d4a4cd4ebc8bc0c4e24baf  
273  7f718ddcc08a28370fbcd1cbe59c4033  fc8b9767454a650e03237161f0f54837  
253  7f718ddcc08a28370fbcd1cbe59c4033  abef6f8501970c985cb3f3160ff1bdab  
220  7f718ddcc08a28370fbcd1cbe59c4033  9ab4f739429d31e57f34e1c037fd2b87  
478  9e32766a84c663a5697fa1564d66b1aa  2fcc8c55ad61684b2e73860522d0626b

In [71]:
len(merge2[merge2.percent_of_positions_retained > 100])

94

In [72]:
len(merge2[merge2.percent_of_positions_retained == 100])

23

In [73]:
merge2[merge2.percent_of_positions_retained > 100].sample(5)

identifier  vp_idx  \
300  0af37e731f00a843fb9a0fe286f8d958/1093524     132   
316  0af37e731f00a843fb9a0fe286f8d958/1093540     121   
180  0af37e731f00a843fb9a0fe286f8d958/1093333      88   
326  0af37e731f00a843fb9a0fe286f8d958/1093550     142   
298  0af37e731f00a843fb9a0fe286f8d958/1093522      74   

                     gtfs_dataset_key  trip_id  number_of_unique_vps_sjoin  \
300  0af37e731f00a843fb9a0fe286f8d958  1093524                         146   
316  0af37e731f00a843fb9a0fe286f8d958  1093540                         133   
180  0af37e731f00a843fb9a0fe286f8d958  1093333                          92   
326  0af37e731f00a843fb9a0fe286f8d958  1093550                         149   
298  0af37e731f00a843fb9a0fe286f8d958  1093522                         133   

     percent_of_positions_retained                          feed_key  \
300                         110.61  7f718ddcc08a28370fbcd1cbe59c4033   
316                         109.92  7f718ddcc08a28370fbcd1cbe59c4033   
180                         104.55  7f718ddcc08a28370fbcd1cbe59c4033   
326                         104.93  7f718ddcc08a28370fbcd1cbe59c4033   
298                         179.73  7f718ddcc08a28370fbcd1cbe59c4033   

                      shape_array_key  
300  34655f8638fe2c2033d7bbb20b368972  
316  7522dcf861b71950ebce7fc12d3b7e61  
180  8076d7952960911d870a90823e0e30c5  
326  e66ccd7bc3be2e9b30de3ad407ed42b3  
298  34655f8638fe2c2033d7bbb20b368972

#### Merge test2 with A1sjoin

In [74]:
test2.sample()

_gtfs_dataset_name  \
5566  Bay Area 511 Emery Go-Round VehiclePositions   

             schedule_gtfs_dataset_key      trip_id  \
5566  12a04922f8e3a4622fbefc232ff191b0  13_Trip5_SP   

                     trip_instance_key        location_timestamp  \
5566  bb086f8bc08530bfc74c1e53fb50600b 2023-07-13 02:12:13+00:00   

     location_timestamp_local  hour                  gtfs_dataset_key       x  \
5566      2023-07-12 19:12:13    19  0faa34840bb65e96b7f83b7f379c2edd -122.31   

         y  vp_idx  
5566 37.84  108977

In [75]:
vp_to_seg.sample()

vp_idx                   shape_array_key  stop_sequence
129953  8085824  63309472f9d07c565fdec738624ec4ef             22

In [76]:
len(vp_to_seg)

24973725

In [77]:
len(test2)

101162

In [78]:
# pd.merge(test2, vp_to_seg, on = ['vp_idx'], how = 'outer', indicator = True)[['_merge']].value_counts()

In [79]:
# test2 is all usable VPS (a subset)
# vp_to_seg are sjoin stuff
# use a left join because these are the vps that were not properly joned
merge3 = pd.merge(test2,vp_to_seg, on = ['vp_idx'], how = 'left', indicator = True)

In [80]:
merge3._merge.value_counts()

both          128205
left_only      21130
right_only         0
Name: _merge, dtype: int64

In [81]:
agg1 = merge3.groupby(['gtfs_dataset_key','trip_id','_merge']).agg({'trip_instance_key':'count'}).reset_index()

In [82]:
len(agg1)

10080

In [83]:
agg1['left_only'] = None

In [84]:
agg1['both'] = None

In [85]:
agg1['pts_not_in_sjoin'] = np.where(agg1._merge == 'left_only', agg1.trip_instance_key, agg1.left_only)

In [86]:
agg1['sjoin_pts'] = np.where(agg1._merge == 'both', agg1.trip_instance_key, agg1.both)

In [87]:
agg1.pts_not_in_sjoin =agg1.pts_not_in_sjoin.fillna(0)

In [88]:
agg1.sjoin_pts =agg1.sjoin_pts.fillna(0)

In [89]:
len(agg1)

10080

In [90]:
agg2 = agg1.sort_values(['trip_id','left_only','both'], ascending = False).drop_duplicates(['trip_id'])

In [91]:
agg2 = (agg1
            .groupby(['gtfs_dataset_key','trip_id'])
            .agg({'pts_not_in_sjoin':'sum','sjoin_pts':'sum'})
            .reset_index()
           )

In [92]:
agg2 = agg2.sort_values(['pts_not_in_sjoin','sjoin_pts'], ascending = False).drop_duplicates(['trip_id'])

In [93]:
agg2['all_pts'] = agg2.pts_not_in_sjoin + agg2.sjoin_pts

In [94]:
agg2['percent_of_pts'] = agg2.sjoin_pts/agg2.all_pts * 100

In [95]:
len(agg2)

672

In [96]:
agg2.percent_of_pts.describe()

count   672.00
mean     81.53
std      30.13
min       0.00
25%      77.89
50%      95.59
75%     100.00
max     100.00
Name: percent_of_pts, dtype: float64

In [97]:
agg2.sample(10)

gtfs_dataset_key                 trip_id  \
1379  0af37e731f00a843fb9a0fe286f8d958                 1093332   
1341  00accf770009aafd5dc103ff2eeddb37  t_5635241_b_80735_tn_0   
1466  0af37e731f00a843fb9a0fe286f8d958                 1093455   
1243  00accf770009aafd5dc103ff2eeddb37  t_5634903_b_80735_tn_0   
2483  00e412908245377894949d292fb79610  t_1522822_b_30719_tn_0   
1252  00accf770009aafd5dc103ff2eeddb37  t_5634925_b_80735_tn_0   
1555  0af37e731f00a843fb9a0fe286f8d958                 1093597   
1309  00accf770009aafd5dc103ff2eeddb37  t_5635121_b_80735_tn_0   
2484  00e412908245377894949d292fb79610  t_1522823_b_30719_tn_0   
1424  0af37e731f00a843fb9a0fe286f8d958                 1093413   

      pts_not_in_sjoin  sjoin_pts  all_pts  percent_of_pts  
1379                 0        153      153          100.00  
1341                 3         56       59           94.92  
1466                 0        187      187          100.00  
1243                 1         88       89           98.88  
2483                 3         41       44           93.18  
1252                 0        159      159          100.00  
1555                97        182      279           65.23  
1309                33        605      638           94.83  
2484                 5         54       59           91.53  
1424                 0        100      100          100.00

In [98]:
#test2[(test2.gtfs_dataset_key == "1a5a0ff50ac6b3f4fa4ee1b7b9b7c205") & (test2.trip_id == '198')].shape

In [99]:
#merge3[(merge3.gtfs_dataset_key == "1a5a0ff50ac6b3f4fa4ee1b7b9b7c205") & (merge3.trip_id == '198')].shape

In [100]:
#merge3[(merge3.gtfs_dataset_key == "1a2ad6d1b3f6621e73730db90f2e8051") & (merge3.trip_id == '5_Trip9_H_COVID')].shape

In [101]:
#vp_to_seg.sample()

#### Compare results

In [102]:
agg2.sample()

gtfs_dataset_key      trip_id  pts_not_in_sjoin  \
2966  0faa34840bb65e96b7f83b7f379c2edd  14_Trip3_SP                56   

      sjoin_pts  all_pts  percent_of_pts  
2966        245      301           81.40

In [103]:
merge2.sample()

identifier  vp_idx  \
108  00e412908245377894949d292fb79610/t_1523699_b_30719_tn_0      98   

                     gtfs_dataset_key                 trip_id  \
108  00e412908245377894949d292fb79610  t_1523699_b_30719_tn_0   

     number_of_unique_vps_sjoin  percent_of_positions_retained  \
108                         109                         111.22   

                             feed_key                   shape_array_key  
108  99f52a915560a1341f44dc11decfeeaa  65fb5eb3986850f5107685acae0d6cbf

In [104]:
merge4 = pd.merge(agg2, merge2, on = ['gtfs_dataset_key','trip_id'], how = 'inner')

In [105]:
merge4['difference'] = (merge4.percent_of_pts - merge4.percent_of_positions_retained)

In [106]:
merge4.difference.describe()

count     512.00
mean       -0.92
std        64.96
min     -1237.50
25%         0.00
50%         4.47
75%        11.16
max        80.38
Name: difference, dtype: float64

In [107]:
merge4.percent_of_positions_retained.describe()

count    512.00
mean      91.00
std       64.42
min       14.56
25%       69.09
50%       89.52
75%       98.85
max     1275.00
Name: percent_of_positions_retained, dtype: float64

In [108]:
preview_cols = ['shape_array_key','gtfs_dataset_key', 'trip_id', 'pts_not_in_sjoin', 'sjoin_pts', 'all_pts',
        'percent_of_pts', 'vp_idx', 'number_of_unique_vps_sjoin', 'percent_of_positions_retained', 'difference']

##### Test 

Only 26% of points joined
* key = 2a450025e04189713e94821c2a4ef862
* trip_id = W_31_outbound_0655
* shape_key = 8277a929a0875a82430614e2f04aef20



In [109]:
merge4[preview_cols].sample(10)

shape_array_key                  gtfs_dataset_key  \
459  7522dcf861b71950ebce7fc12d3b7e61  0af37e731f00a843fb9a0fe286f8d958   
274  a5d1b6a856479abd264f24b9cec7d1be  00e412908245377894949d292fb79610   
486  69335cca699ea56a2cfc31402e36ced1  0af37e731f00a843fb9a0fe286f8d958   
372  6a3eb4187201e53ec9096fa47f009846  0af37e731f00a843fb9a0fe286f8d958   
472  14a663c742e8ad923c4e323e688563b6  00accf770009aafd5dc103ff2eeddb37   
173  1425c95c43a72622ab1c98372c0cb392  00accf770009aafd5dc103ff2eeddb37   
168  c0bacd67f65c00a8a92f4d8a313ef6f6  00accf770009aafd5dc103ff2eeddb37   
256  b35ca3a9d5da895ceb2f0c596b363d7d  00e412908245377894949d292fb79610   
89   61cb9e7cb1051b1c1460d7e3bec3dec8  0af37e731f00a843fb9a0fe286f8d958   
67   bbcffbd3d0f15bb6aa401323d9b4cc16  0faa34840bb65e96b7f83b7f379c2edd   

                    trip_id  pts_not_in_sjoin  sjoin_pts  all_pts  \
459                 1093544                 0        157      157   
274  t_1524237_b_30719_tn_0                 4        275      279   
486                 1093404                 0        105      105   
372                 1093444                 0        234      234   
472  t_5634935_b_80735_tn_0                 0        129      129   
173  t_5634944_b_80735_tn_0                19        279      298   
168  t_5634919_b_80735_tn_0                21        201      222   
256  t_1523670_b_30719_tn_0                 6        274      280   
89                  1093386                47        191      238   
67              15_Trip2_SP                57        194      251   

     percent_of_pts  vp_idx  number_of_unique_vps_sjoin  \
459          100.00     110                         115   
274           98.57     176                          60   
486          100.00      90                         114   
372          100.00     151                          97   
472          100.00      54                          54   
173           93.62     200                         181   
168           90.54     131                         110   
256           97.86      80                          74   
89            80.25     182                         124   
67            77.29     174                         117   

     percent_of_positions_retained  difference  
459                         104.55       -4.55  
274                          34.09       64.48  
486                         126.67      -26.67  
372                          64.24       35.76  
472                         100.00        0.00  
173                          90.50        3.12  
168                          83.97        6.57  
256                          92.50        5.36  
89                           68.13       12.12  
67                           67.24       10.05

#### All Vehicle Positions

In [110]:
stop running

SyntaxError: invalid syntax (2467127375.py, line 1)

In [ ]:
# VP all without paring
STG_0_FILE = STOP_SEG_DICT['stage0']
    

In [ ]:
f"{STG_0_FILE}_{analysis_date}/"

In [ ]:
all_pts = helpers.import_vehicle_positions(
            SEGMENT_GCS,
            f"{STG_0_FILE}_{analysis_date}/",
            "df",
            columns = ["gtfs_dataset_key", "trip_id","geometry"],
            partitioned = False
        )
all_pts = all_pts.compute()

In [ ]:
all_pts.sample(5)

In [ ]:
all_pts2 = (all_pts
        .groupby(['gtfs_dataset_key','trip_id'])
        .agg({'geometry':'nunique'}).reset_index()
        .rename(columns = {'geometry':'number_of_unique_vps_all_pts'})
        .reset_index(drop = True)
       )

In [ ]:
len(all_pts[(all_pts.gtfs_dataset_key == "cdd2ad81863b6d4ad51676a1cb781ea8") & (all_pts.trip_id == "10686020")])

In [ ]:
all_pts2[(all_pts2.gtfs_dataset_key == "cdd2ad81863b6d4ad51676a1cb781ea8") & (all_pts2.trip_id == "10686020")]

In [ ]:
all_pts2[(all_pts2.gtfs_dataset_key == "593953c37ce48a9449bb90808ba0c1e1") & (all_pts2.trip_id == "t5FE-b3EA-sl13")]

In [ ]:
all_pts2[(all_pts2.gtfs_dataset_key == "65d9589130415c685b89f4f7c2d8bd7e") & (all_pts2.trip_id == "10035002751332-DEC22")]

In [ ]:
# How did this pop up in the grouped df if it doesn't even exist??
all_pts[(all_pts.gtfs_dataset_key == "00accf770009aafd5dc103ff2eeddb37") & (all_pts.trip_id == "-1160024104")]

In [ ]:
all_pts3 = all_pts.drop(columns = ['geometry']).drop_duplicates().reset_index(drop = True)

In [ ]:
len(all_pts3)

In [ ]:
all_pts2.shape

In [ ]:
len(all_pts)

##### Merge Sjoin with All Vehicles

In [ ]:
# Merge to get rid of weird rows??
# These are all points 
pd.merge(all_pts3, all_pts2, on = ['gtfs_dataset_key','trip_id'], how = 'outer', indicator = True)[['_merge']].value_counts()

In [ ]:
merge1 = pd.merge(all_pts3, all_pts2, on = ['gtfs_dataset_key','trip_id'], how = 'inner')

In [ ]:
merge1.sample()

In [ ]:
merge1.shape

In [ ]:
# These are sjoin positions
agg3.sample()

In [ ]:
agg3.shape

In [ ]:
pd.merge(merge1, agg3, on = ['gtfs_dataset_key','trip_id'], how = 'outer', indicator = True)[['_merge']].value_counts()

In [ ]:
merge2 = pd.merge(merge1, agg3, on = ['gtfs_dataset_key','trip_id'], how = 'inner')

In [ ]:
merge2.sample(5)

### Fix 2 - Keep timestamps nearby if there aren't enough points

In [ ]:
stop running

### Investigate - Don't Delete

In [111]:
stage3_df = speed_utils.flag_stage3(divide_by_zero, analysis_date)

2023-07-18 17:16:32.719940
check in stage 2                   253015
repeated timestamps & locations     23545
repeated locations                     12
Name: stage3_flag, dtype: int64
Have to check 91.48250726754696 % of rows in stage 2
Took 0:00:20.313487


In [112]:
stage3_df.shape_array_key.nunique()

2494

In [113]:
sort_by = ['_gtfs_dataset_name','shape_array_key','trip_id','stop_sequence']

In [114]:
preview_cols = sort_by + ['stop_id','gtfs_dataset_key','location_timestamp_local','pair','stage3_flag']

#### Find routes with a lot of n_trips that need to be evaluated.

In [115]:
shape_trips = speed_utils.count_trips_routes(stage3_df)

In [116]:
shape_trips.head(5)

shape_array_key                  _gtfs_dataset_name  \
248087  e22aab342fa9be03e18fbbd8fed80659  Bay Area 511 Muni VehiclePositions   
147323  82e4c946c08a695b0169ed9e3bc1d681  Bay Area 511 Muni VehiclePositions   
62289   3cf4fab74c683cd8c936e5144e4a73d5  Bay Area 511 Muni VehiclePositions   
11051   08f0692fdf4fd09673d6da595695acce  Bay Area 511 Muni VehiclePositions   
58483   3852bca066b78935219798cf7a9472b0  Bay Area 511 Muni VehiclePositions   

                        gtfs_dataset_key       trip_id  n_trips  
248087  c0e3039da063db95ebabd3fe4ee611a4  11359079_M11      160  
147323  c0e3039da063db95ebabd3fe4ee611a4  11384062_M11      155  
62289   c0e3039da063db95ebabd3fe4ee611a4  11355247_M11      149  
11051   c0e3039da063db95ebabd3fe4ee611a4  11348579_M11      149  
58483   c0e3039da063db95ebabd3fe4ee611a4  11355137_M11      146

#### Example Trip 1
* Understanding the result from flag_stage3().
* Looking at AC Transit: stop sequences 6 and 7 have different stop_ids. However, their time stamps and locations are the same.
* It looks like they share the same point.
* However, this isn't due to paring too many points: there just aren't enough points to choose from in the raw data.
* Also sequence 2 is extremely long.

In [117]:
test_route1 = "e22aab342fa9be03e18fbbd8fed80659"
test_gtfs_key1 = "c0e3039da063db95ebabd3fe4ee611a4"
test_trip1 = "11359079_M11"

In [118]:
# % of trips with problematic rows for this route
trips_count[trips_count.shape_array_key == test_route1]

shape_array_key  all_trips  trips_with_zero  \
3619  e22aab342fa9be03e18fbbd8fed80659        164            50.00   

      percent_of_trips_with_problematic_rows  
3619                                   30.49

In [119]:
speed_utils.original_df_rows(flagged, test_trip1, test_route1)

stop_sequence stop_id  meters_elapsed  sec_elapsed
2229760              1   15926            0.00       608.00
2229923              2   15791          121.71       669.00
2230184              3   15781            0.00        31.00
2230339              4   15805            0.00        31.00
2230381              5   15800            0.00        30.00
2230735              7   15801            0.00        15.00
2230914              8   15586            0.00         0.00
2231009              9   15620          178.84        75.00
2231172             10   15624          224.47        31.00
2231315             11   15605            0.00        45.00
2231472             12   15613            0.00         0.00
2231689             13   15596           72.52        45.00
2231896             15   15583           74.73        61.00
2232058             16   15571           12.38        46.00
2232288             17   17841          177.96        46.00
2232433             18   15567            0.00        45.00
2232611             19   15565            0.00        45.00
2232649             20   15561          202.76       107.00
2232778             21   15557            0.00        15.00
2232992             22   15553          225.97        91.00
2233229             23   15551            1.44        45.00
2233340             24   15547          296.91        91.00
2233601             26   18088          160.61       151.00
2233745             27   18089          449.77       151.00
2233918             28   18090          317.10       107.00
2234096             29   18091           72.79        45.00
2234248             30   18092          204.34       106.00
2234348             31   18093          405.94       166.00
2234524             32   18094          267.86       106.00
2234693             33   18095            0.00        45.00
2234801             34   18096            0.00        46.00
2234924             35   16800           16.33        45.00
2235151             36   16806          167.42        46.00
2235244             37   16820           60.48      1135.00

In [120]:
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = test_route1,
                        trip = test_trip1,
                        gtfs_key = test_gtfs_key1)

ALL POINTS


SJOIN


FIRST AND LAST


#### Example Trip 2
* Underestanding the result from `flag_stage3()`. 
* Same thing as Ex Trip 1 except kooking at LA Metro: stop sequences 45 and 46 have different stop_ids. However, their time stamps and locations are the same. 
* Same issue: segments 45 and 46 are sharing points. There aren't enough points captured.
* In general, it looks like this route doesn't have a lot of rows that are ok.

In [121]:
test_route2 = "38c814829dff816aa87c606c3aab4f45"
test_gtfs_key2 = "65d9589130415c685b89f4f7c2d8bd7e"
test_trip2 = "10294000051654-DEC22"

In [122]:
# Original number of rows for this trip
len(flagged[(flagged.trip_id == test_trip2) & (flagged.shape_array_key == test_route2)])

0

In [123]:
# Rows with zeroes...a lot of them.
len(divide_by_zero[(divide_by_zero.trip_id == test_trip2) & (divide_by_zero.shape_array_key == test_route2)])

0

In [124]:
stage3_df[(stage3_df.stage3_flag != 'check in stage 2') & (stage3_df.shape_array_key == test_route2) 
   & (stage3_df.stop_sequence.isin([45,46]))].sort_values(by =sort_by)[preview_cols]

Empty DataFrame
Columns: [_gtfs_dataset_name, shape_array_key, trip_id, stop_sequence, stop_id, gtfs_dataset_key, location_timestamp_local, pair, stage3_flag]
Index: []

In [125]:
# % of trips with problematic rows for this route, lots of them
trips_count[trips_count.shape_array_key == test_route2]

Empty DataFrame
Columns: [shape_array_key, all_trips, trips_with_zero, percent_of_trips_with_problematic_rows]
Index: []

In [126]:
#speed_utils.original_df_rows(m1, test_trip2, test_route2)

In [127]:
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = test_route2,
                        trip = test_trip2,
                        gtfs_key = test_gtfs_key2,)

ValueError: Location values cannot contain NaNs.

In [ ]:
# See which trip has the most rows that are ok for this route
route_most_populated_df[route_most_populated_df.shape_array_key == test_route2]

In [ ]:
# Plot the trip from this route with the highest % of ok rows
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = test_route2,
                        trip = "10294000051724-DEC22",
                        gtfs_key = test_gtfs_key2,)

#### Example Trip 3
* Choosing a route/trip with high n_trips that isn't Muni or LA Metro to shake things up.
* San Diego Vehicle Positions
* Segments 44 and 45 don't have any rows in the original dataframe for trip 16938440.

In [ ]:
test_route3 = "1fc55d9df0cd785dddc864bf1b72976f"
test_gtfs_key3 = "a4f6fd5552107e05fe9743ac7cce2c55"
test_trip3 = "16938440"

In [ ]:
stage3_df[(stage3_df.shape_array_key == test_route3) & (stage3_df.trip_id == test_trip3)].sort_values(by =sort_by)[preview_cols]

In [ ]:
speed_utils.original_df_rows(flagged, test_trip3, test_route3)

In [ ]:
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = test_route3,
                        trip = test_trip3,
                        gtfs_key = test_gtfs_key3,)

In [ ]:
# Trip from this route with the most ok rows
route_most_populated_df[route_most_populated_df.shape_array_key == test_route3]

In [ ]:
# Test the trip with the most ok rows
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = test_route3,
                        trip = "16938341",
                        gtfs_key = test_gtfs_key3,)

In [ ]:
speed_utils.original_df_rows(flagged, "16938341", test_route3)

#### Example Trip 4

In [128]:
gtfs_key4 = "2a450025e04189713e94821c2a4ef862"
trip_id4= "W_31_outbound_0655"
shape_key4 = "8277a929a0875a82430614e2f04aef20"

In [129]:
speed_utils.original_df_rows(flagged, trip_id4, shape_key4)

stop_sequence stop_id  meters_elapsed  sec_elapsed
1306637              2   22169          202.88        32.00
1306648              3   22000          220.91        46.00
1306687              4   22002          279.46        52.00
1306705              5   22004          221.85        82.00
1306717              6   22035          469.41        33.00
1306749              7   22037          134.31        11.00
1306761              8   22041            0.00         0.00
1306782              9   22297          205.74        23.00
1306803             10   22174          362.94        32.00
1306838             11   22254          264.13        39.00
1306861             12   22255          203.57        50.00

In [130]:
len(speed_utils.original_df_rows(flagged, trip_id4, shape_key4))

11

In [131]:
# Test the trip with the most ok rows
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = shape_key4,
                        trip = trip_id4,
                        gtfs_key = gtfs_key4,)

ALL POINTS


SJOIN


FIRST AND LAST


#### Example Trip 5
316 total points, 210 sjoin points - 66% joined.
266 total points, 133 sjoin points - 50% joined.
* route5 = "df6aff9f6c51360bdf4819865e53681d"
* operator5 = "0af37e731f00a843fb9a0fe286f8d958"
* trip5 = "1093295"

In [141]:
preview_cols2 = ['shape_array_key','gtfs_dataset_key', 'trip_id', 'pts_not_in_sjoin', 'sjoin_pts', 'all_pts',
        'percent_of_pts', 'vp_idx', 'number_of_unique_vps_sjoin', 'percent_of_positions_retained', 'difference']

In [142]:
merge4[merge4.trip_id == "1093295"][preview_cols2]

shape_array_key                  gtfs_dataset_key  \
31  df6aff9f6c51360bdf4819865e53681d  0af37e731f00a843fb9a0fe286f8d958   

    trip_id  pts_not_in_sjoin  sjoin_pts  all_pts  percent_of_pts  vp_idx  \
31  1093295               106        210      316           66.46     266   

    number_of_unique_vps_sjoin  percent_of_positions_retained  difference  
31                         133                          50.00       16.46

In [133]:
route5 = "df6aff9f6c51360bdf4819865e53681d"
operator5 = "0af37e731f00a843fb9a0fe286f8d958"
trip5 = "1093295"

In [134]:
# Test the trip with the most ok rows
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = route5,
                        trip = trip5,
                        gtfs_key = operator5,)

ALL POINTS


SJOIN


FIRST AND LAST


#### Example Trip 6
* Appraently 231% of positions retained, 104 vehicle positions in sjoin but 45 in original. 

In [135]:
route6= "f58e4b0dbcdb35bdfa681f6cac38330a"
operator6 = "0af37e731f00a843fb9a0fe286f8d958"
trip6 = "1093314"

In [143]:
merge4[merge4.trip_id == trip6][preview_cols2]

shape_array_key                  gtfs_dataset_key  \
510  f58e4b0dbcdb35bdfa681f6cac38330a  0af37e731f00a843fb9a0fe286f8d958   

     trip_id  pts_not_in_sjoin  sjoin_pts  all_pts  percent_of_pts  vp_idx  \
510  1093314                 0         54       54          100.00      45   

     number_of_unique_vps_sjoin  percent_of_positions_retained  difference  
510                         104                         231.11     -131.11

In [136]:
speed_utils.stage2_trouble_shooting(flagged_df= stage3_df,
                        date = analysis_date,
                        route = route6,
                        trip = trip6,
                        gtfs_key = operator6,)

ALL POINTS


SJOIN


FIRST AND LAST
